# Homework 7

Projection and portfolio Optimization

In [1]:
using LinearAlgebra, DataFrames, Statistics, StatsPlots, YFinance, Dates, CSV

## 1 Projection onto a halfspace

A nonzero n-vector $a$ and a scalar $\beta$ define the halfspace $$
H^{-}_{a,β}=\{\,x∈\mathbb R^n\mid ⟨a,x⟩≤β\,\}.
$$

### 1.1 Derive the expression for the projection

Derive an explicit expression for projecting an arbitrary n-vector b
onto the halfspace $H^-_{a,β}$.

### 1.2 Implement the projection

Implement your derived solution by completing the following function.

``` julia
"""
Project the n-vector `b` onto the halfspace {x ∣ ⟨a,x⟩ ≤ β} defined by the nonzero vector `a` and the scalar `β`.
"""
function proj_halfspace(b, a, β)
  # your code here
end;
```

### 1.3 Implement a unit test

Verify numerically with a simple example that your projection code is
correct. Formal verification is not required.

``` julia
function test_proj_halfspace()
    a = ...
    β = ...
    b = ...
    expected = ...
    result = proj_halfspace(b, a, β)
    result == expected
end
test_proj_halfspace()
```

## 2 Alternating projection method

The function `projsplx`, defined here, computes the projection of any
$n$-vector onto the probability simplex
$\{x\in\mathbb R^n\mid \sum_j^nx_j=1,\ x≥0\}$.

In [1]:
"""
Projection onto the unit simplex.

    projsplx(b) -> x

Variant of `projsplx`.
"""
function proj_simplex(b::Vector; τ=1.0)
    x = copy(b)
    projsplx!(x, τ)
    return x
end;

"""
Projection onto the unit simplex {x | sum(x) = τ, x ≥ 0}.

    projsplx!(b, τ)

In-place variant of `projsplx`.
"""
function projsplx!(b::Vector{T}, τ::T) where T

    n = length(b)
    bget = false

    idx = sortperm(b, rev=true)
    tsum = zero(T)

    @inbounds for i = 1:n-1
        tsum += b[idx[i]]
        tmax = (tsum - τ)/i
        if tmax ≥ b[idx[i+1]]
            bget = true
            break
        end
    end

    if !bget
        tmax = (tsum + b[idx[n]] - τ) / n
    end

    @inbounds for i = 1:n
        b[i] = max(b[i] - tmax, 0)
    end
end;

The cell below demonstrates the projection of a vector `b` onto the
simplex.

In [1]:
let
    b = [12.0, -23.0, 16.0]
    x = proj_simplex(b)
end

3-element Vector{Float64}:
 0.0
 0.0
 1.0

Now, suppose we want to compute the projection onto the **intersection**
of the probability simplex and an arbitrary halfspace. Can we achieve
this using the projection functions `proj_halfspace` and `proj_simplex`?

Yes, we can use the **[Projection Onto Convex
Sets](https://en.wikipedia.org/wiki/Projections_onto_convex_sets)**
algorithm, which projects onto the intersection of convex sets
$C_1\bigcap C_2$ by itereratively projecting onto $C_1$ and $C_2$. The
algorithm is straightforward and involves the following iteration:

$$x_{k+1}=P_1(P_2(x_k)),$$

where $P_1$ and $P_2$ are projection operators onto the sets $C_1$ and
$C_2$, respectively. Implement this algorithm for generic projection
operators $P_1$ and $P_2$. Exit the loop when
$$\|x_{k+1}-x_k\|≤ϵ\|x_0\|$$ for some positive tolerance $\epsilon$.

Note that this method can in some situations require many iterations.
However, since we’re dealing with a small problem, this should not be an
issue.

### 2.1 Implement the intersection projection

Complete the following function.

``` julia
"""
Project a vector `x` onto the intersection of two convex sets. Takes as input two functions `p1` and `p2` that each take a vector and return the projection of `b0` onto the corresponding sets.
"""
function proj_intersection(x::Vector, p1::Function, p2::Function; maxits=100, ϵ=1e-7)
    err = []
    x0 = copy(x)
    ϵ *= norm(x0, Inf)
    for i ∈ 1:maxits
        # your code here
        push!(err, norm(x-x0, Inf))
        err[end] ≤ ϵ && break
        x0 = copy(x)
    end
    return x
end;
```

### 2.2 Implement a unit test

Test your implementation of `proj_intersection` on a small problem that
aims to find the projection of a vector onto the intersection of the
unit probability simplex and a halfspace. Verify that the answer is
correct.

> **Warning**
>
> Make sure that your test problem is **feasible** – i.e., that the
> intersection isn’t empty.

## 3 Financial portfolio optimization

[Modern portfolio optimization
theory](http://en.wikipedia.org/wiki/Modern_portfolio_theory) is based
on the [Markovitz](http://en.wikipedia.org/wiki/Harry_Markowitz) model
for determining a portfolio of stocks with a desired expected rate of
return that has the smallest amount of risk, as measured by the variance
of the portfolio’s return. The main idea is that by *diversifying*
(i.e., investing in a mixture of different stocks), one can guard
against large amounts of variance in the rates of return of the
individual stocks in the portfolio.

### Rate of return and risk

Suppose that $p_1,\ldots,p_m$ are the historical prices of a stock over
some period of time. We define the *rPPate of return* at time $t$,
relative to the intial price $p_1$ by <span id="eq-rate-of-return">$$
r_t := (p_t-p_1)/p_1, \quad t=1,\ldots,m.
 \qquad(1)$$</span>

The *expected rate of return* is the mean $\mu$ of the rates of return.
The *risk* of the portfolio is measured as the standard deviation
$\sigma$ of the rates of return: $$
\mu := \frac{1}{m}\sum_{t=1}^m r_t,
\quad\text{and}\quad
\sigma:=\sqrt{\frac{1}{m}\sum_{t=1}^m (r_t-\mu)^2}.
$$

Given a collection of $n$ stocks, let $r_t^i$ be the rate of return of
stock $i$ at time $t$. Let $r$ be the $n$-vector of the expected rates
of return of the $n$ stocks. In addition, let $\Sigma$ be the
$n\times n$ *covariance matrix* of the rates of return of the $n$
stocks. Thus, $r_i$ is the mean of the rates of return of stock $i$, the
$i$th diagonal element $\Sigma_{ii}$ is its variance, and $\Sigma_{ij}$
is the covariance of the rates of return of stocks $i$ and $j$, i.e., $$
r_i:=\frac{1}{m}\sum_{t=1}^m r_t^i
\quad\text{and}\quad
\Sigma_{ij}:=\frac{1}{m}\sum_{t=1}^m (r_t^i-r_i)(r_t^j-r_j).
$$

### Portfolio expected return and risk

We let $x_i$ be the fraction of our investment money we put into stock
$i$, for $i=1,\ldots,n$. For the sake of this study, we assume there is
no *short selling* (i.e., holding a stock in negative quantity.) Thus,
$x=(x_1,\ldots,x_n)$ is a vector of length $n$ that has nonnegative
entries that sum to one (i.e, $x\ge0$ and $\sum_{i=1}^n x_i=1$). The
vector $x$ represents our portfolio of investments. The expected rate of
return and standard deviation of a portfolio $x$ are then given by $$
\mu:= r^T x \quad\text{and}\quad \sigma:=\sqrt{x^T\Sigma x}.
$$

The code below downloads one year (2022-2023) of historical prices of a
collection of stocks and implements `meancov`, which computes the
expected rate of return and covariance matrix of the rates of return.

In [1]:
stocks = [
    "AAPL", "META", "GOOG", "MSFT", "NVDA",  # technology
    "AMZN", "COST", "EBAY", "TGT", "WMT",    # services
    "BMO", "BNS", "HBCP", "RY", "TD",        # finance
    "BP", "CVX", "IMO", "TTE", "XOM"         # energy
]

# Calculate dates for one year of data
end_date = today()
start_date = end_date - Year(1)

# Create cache directory if it doesn't exist
cache_dir = joinpath(@__DIR__, "cache")
mkpath(cache_dir)

"""
    fetch_and_process_stock(symbol::String, start_date::Date, end_date::Date, cache_dir::String) -> DataFrame

Fetch stock data for the given symbol and process it to calculate relative returns from the first day.
If cached data exists and is recent enough, use that instead of downloading.

Returns a DataFrame with columns `Date` and `relative returns`.
"""
function fetch_and_process_stock(symbol::String, start_date::Date, end_date::Date, cache_dir::String)
    cache_file = joinpath(cache_dir, "$(symbol)_$(start_date)_$(end_date).csv")
    
    # Use cache if it exists and is recent (less than 1 day old)
    if isfile(cache_file) && (time() - mtime(cache_file)) < 24*60*60
        df = DataFrame(CSV.File(cache_file))
        return df
    end
    
    # Get daily stock data
    stock_data = get_prices(
        symbol,
        startdt=start_date,
        enddt=end_date,
        interval="1d"
    )
    
    # Convert to DataFrame and process
    df = DataFrame(stock_data)
    
    # Calculate relative returns
    initial_price = first(df.adjclose)
    df[!, symbol] = @. (df.adjclose - initial_price) / initial_price
    
    # Keep only date and relative returns
    select!(df, :timestamp => :Date, symbol)
    
    # Save to cache
    CSV.write(cache_file, df)
    
    return df
end

# Fetch and process all stocks
df = mapreduce(
    s -> fetch_and_process_stock(s, start_date, end_date, cache_dir),
    (x, y) -> innerjoin(x, y, on=:Date),
    stocks
)

"""
    meancov(df) -> Tuple{Vector{Float64}, Matrix{Float64}}

Compute the expected rate of return and covariance matrix from a DataFrame of stock returns.

Returns:
- r: Vector of expected returns for each stock
- Σ: Covariance matrix of returns
"""
function meancov(df)
    r = mean.(eachcol(df[:,2:end]))
    Σ = cov(Matrix(df[:,2:end]))
    return r, Σ
end

Here are the expected rates of return for each stock.

In [1]:
r, Σ = meancov(df)
df_plot = DataFrame(stock=stocks, r=r, risk=diag(Σ))
sort!(df_plot, :r)

# Create primary y-axis for returns
p = @df df_plot bar(:stock, :r, legend=false, ylabel="Return", title="Returns and Risk of Stocks")
xlabel!("Stock")

# Add secondary y-axis for risk
p2 = twinx(p)
@df df_plot scatter!(p2, :stock, :risk, color=:red, markersize=4, 
                   marker=:circle, label="Risk", legend=:topleft)
ylabel!(p2, "Risk (Variance)")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip100)" d="M495.353 1782.32 L495.353 1794.98 L502.853 1794.98 Q506.626 1794.98 508.432 1793.43 Q510.26 1791.85 510.26 1788.64 Q510.26 1785.4 508.432 1783.87 Q506.626 1782.32 502.853 1782.32 L495.353 1782.32 M495.353 1768.1 L495.353 1778.52 L502.274 1778.52 Q505.7 1778.52 507.367 1777.25 Q509.057 1775.95 509.057 1773.31 Q509.057 1770.7 507.367 1769.4 Q505.7 1768.1 502.274 1768.1 L495.353 1768.1 M490.677 1764.26 L502.622 1764.26 Q507.969 1764.26 510.862 1766.48 Q513.756 1768.71 513.756 1772.8 Q513.756 1775.97 512.274 1777.85 Q510.793 1779.72 507.922 1780.19 Q511.372 1780.93 513.27 1783.29 Q515.191 1785.63 515.191 1789.15 Q515.191 1793.77 512.043 1796.3 Q508.895 1798.82 503.085 1798.82 L490.677 1798.82 L490.677 1764.26 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip100)" d="M889.094 1766.92 L889.094 1771.85 Q886.733 1769.65 884.048 1768.57 Q881.386 1767.48 878.377 1767.48 Q872.451 1767.48 869.303 1771.11 Q866.154 1774.72 866.154 1781.58 Q866.154 1788.4 869.303 1792.04 Q872.451 1795.65 878.377 1795.65 Q881.386 1795.65 884.048 1794.56 Q886.733 1793.47 889.094 1791.27 L889.094 1796.16 Q886.64 1797.83 883.886 1798.66 Q881.154 1799.49 878.099 1799.49 Q870.252 1799.49 865.738 1794.7 Q861.224 1789.89 861.224 1781.58 Q861.224 1773.24 865.738 1768.45 Q870.252 1763.64 878.099 1763.64 Q881.201 1763.64 883.932 1764.47 Q886.687 1765.28 889.094 1766.92 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip100)" d="M1099.09 1767.43 Q1094 1767.43 1090.99 1771.23 Q1088 1775.02 1088 1781.58 Q1088 1788.1 1090.99 1791.9 Q1094 1795.7 1099.09 1795.7 Q1104.18 1795.7 1107.15 1791.9 Q1110.13 1788.1 1110.13 1781.58 Q1110.13 1775.02 1107.15 1771.23 Q1104.18 1767.43 1099.09 1767.43 M1099.09 1763.64 Q1106.36 1763.64 1110.71 1768.52 Q1115.06 1773.38 1115.06 1781.58 Q1115.06 1789.75 1110.71 1794.63 Q1106.36 1799.49 1099.09 1799.49 Q1091.8 1799.49 1087.42 1794.63 Q1083.07 1789.77 1083.07 1781.58 Q1083.07 1773.38 1087.42 1768.52 Q1091.8 1763.64 1099.09 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip100)" d="M1324.69 1767.43 Q1319.59 1767.43 1316.58 1771.23 Q1313.6 1775.02 1313.6 1781.58 Q1313.6 1788.1 1316.58 1791.9 Q1319.59 1795.7 1324.69 1795.7 Q1329.78 1795.7 1332.74 1791.9 Q1335.73 1788.1 1335.73 1781.58 Q1335.73 1775.02 1332.74 1771.23 Q1329.78 1767.43 1324.69 1767.43 M1324.69 1763.64 Q1331.96 1763.64 1336.31 1768.52 Q1340.66 1773.38 1340.66 1781.58 Q1340.66 1789.75 1336.31 1794.63 Q1331.96 1799.49 1324.69 1799.49 Q1317.4 1799.49 1313.02 1794.63 Q1308.67 1789.77 1308.67 1781.58 Q1308.67 1773.38 1313.02 1768.52 Q1317.4 1763.64 1324.69 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip100)" d="M1677.51 1782.62 Q1679.02 1783.13 1680.43 1784.79 Q1681.87 1786.46 1683.3 1789.38 L1688.05 1798.82 L1683.02 1798.82 L1678.6 1789.96 Q1676.89 1786.48 1675.27 1785.35 Q1673.67 1784.21 1670.89 1784.21 L1665.8 1784.21 L1665.8 1798.82 L1661.12 1798.82 L1661.12 1764.26 L1671.68 1764.26 Q1677.61 1764.26 1680.52 1766.74 Q1683.44 1769.21 1683.44 1774.21 Q1683.44 1777.48 1681.91 1779.63 Q1680.41 1781.78 1677.51 1782.62 M1665.8 1768.1 L1665.8 1780.37 L1671.68 1780.37 Q1675.06 1780.37 1676.77 1778.82 Q1678.51 1777.25 1678.51 1774.21 Q1678.51 1771.18 1676.77 1769.65 Q1675.06 1768.1 1671.68 1768.1 L1665.8 1768.1 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip100)" d="M1847.71 1766.92 L1847.71 1771.85 Q1845.34 1769.65 1842.66 1768.57 Q1840 1767.48 1836.99 1767.48 Q1831.06 1767.48 1827.91 1771.11 Q1824.77 1774.72 1824.77 1781.58 Q1824.77 1788.4 1827.91 1792.04 Q1831.06 1795.65 1836.99 1795.65 Q1840 1795.65 1842.66 1794.56 Q1845.34 1793.47 1847.71 1791.27 L1847.71 1796.16 Q1845.25 1797.83 1842.5 1798.66 Q1839.77 1799.49 1836.71 1799.49 Q1828.86 1799.49 1824.35 

> **In-class: Stock Analysis - NVDA**
>
> Let’s examine NVIDIA (NVDA) stock in more detail — it’s been one of
> the most talked-about technology stocks in recent years because of AI
> advancements.
>
> ``` julia
> # Extract NVDA data
> nvda_idx = findfirst(s -> s == "NVDA", stocks)
> nvda_returns = df[:, nvda_idx+1] # +1 because first column is Date
>
> # Calculate rate of return and risk
> nvda_return = mean(nvda_returns)
> nvda_risk = var(nvda_returns)
>
> println("NVDA Rate of Return: ...")
> println("NVDA Risk (Variance): ...")
> ```
>
> > **Clicker Question 1**
> >
> > What is the approximate rate of return for NVDA over the past year?
> >
> > 1.  33%
> > 2.  34%
> > 3.  35%
> > 4.  36%

### 3.1 Markowitz model

The Markowitz portfolio optimization model finds the allocation of
investments across $n$ stocks that minimizes risk while achieving a
target expected return $\mu$. The model is formulated as: $$
\min_{x}\ \set{\tfrac{1}{2} x^T \Sigma x \mid r^T x \ge \mu,\ x \ge 0,\ \sum_{i=1}^n x_i = 1}
$$ Here, $\Sigma$ is the covariance matrix representing risk, $r$
contains the expected returns of each stock, and $x$ represents the
portfolio weights. The constraints ensure the portfolio achieves the
target return $\mu$, maintains non-negative weights (no short-selling),
and fully allocates the investment (weights sum to 1). The objective
function minimizes portfolio variance subject to these constraints,
balancing risk and return.

> **In-class: Solving the Markowitz Model with Convex.jl**
>
> In this exercise, we’ll implement the Markowitz portfolio optimization
> model using Convex.jl, which provides a domain-specific language for
> expressing convex optimization problems, and COSMO.jl as our solver.
>
> First, let’s install and load the necessary packages:
>
> ``` julia
> # Install packages if needed
> # using Pkg
> # Pkg.add(["Convex", "COSMO"])
>
> using Convex, COSMO
> ```
>
> Now, let’s formulate the Markowitz portfolio optimization problem
> using Convex.jl. We’ll create a function that takes in the expected
> returns `r`, covariance matrix `Σ`, and target return `μ`:
>
> ``` julia
> """
> Solve the Markowitz portfolio optimization model using Convex.jl.
>
> Given a set of assets with expected returns `r` and covariance matrix `Σ`,
> find the portfolio with minimum risk (variance)
> that achieves a target return of `μ`.
>
> Returns the optimal portfolio weights.
> """
> function markowitz_portfolio(r, Σ, μ)
>     n = length(r)
>     
>     # Define variables
>     x = Variable(n)
>     
>     # Define objective: minimize risk (variance)
>     # Hint: Use quadform() function to represent the quadratic term x'Σx
>     objective = # Your code here
>     
>     # Define constraints
>     constraints = [
>         # 1. Expected return constraint: portfolio return ≥ μ
>         # 2. Budget constraint: sum of weights = 1
>         # 3. No short selling: all weights ≥ 0
>         # Your code here
>     ]
>     
>     # Create problem
>     problem = minimize(objective, constraints)
>     
>     # Solve the problem with a silent optimizer
>     solve!(problem, () -> COSMO.Optimizer(verbose=false), silent=true)
>     
>     # Return optimal portfolio weights
>     return evaluate(x)
> end;
> ```
>
> Use your solution to the previous question to solve the problem for a
> target return of 10% using our stock data:
>
> ``` julia
> # Solve for target return of 10%
> target_return = 0.10
> optimal_weights = markowitz_portfolio(r, Σ, target_return)
>
> # Calculate the achieved return and risk
> achieved_return = dot(r, optimal_weights)
> achieved_risk = sqrt(optimal_weights' * Σ * optimal_weights)
>
> println("Optimal portfolio:")
> println("Target return: $(round(target_return * 100, digits=2))%")
> println("Achieved return: $(round(achieved_return * 100, digits=2))%")
> println("Portfolio risk (std dev): $(round(achieved_risk, digits=4))")
> ```
>
>     Optimal portfolio:
>     Target return: 10.0%
>     Achieved return: 10.0%
>     Portfolio risk (std dev): 0.0312
>
> > **Clicker Question 2**
> >
> > Which stock has the highest weight in the optimal portfolio?
> >
> > 1.  NVDA
> > 2.  META
> > 3.  GOOG
> > 4.  TTE
>
> <!-- Let's visualize the portfolio allocation:
>
>
>
>
>
>
>
> ```lzatueh
> # Create a dataframe for better visualization
> portfolio_df = DataFrame(
>     Stock = stocks,
>     Weight = round.(optimal_weights * 100, digits=2)
> )
>
> # Sort by weight for better visualization
> sort!(portfolio_df, :Weight, rev=true)
>
> # Only display stocks with weight > 0.5%
> filter!(row -> row.Weight > 0.5, portfolio_df)
>
> # Display as a table
> portfolio_df
>
> # Visualize as a pie chart
> pie(portfolio_df.Stock, portfolio_df.Weight, 
>     title="Optimal Portfolio Allocation (Weights > 0.5%)")
> ```
>
>
>
>
>
>
> ::: -->

### 3.2 Implement a projected gradient minimizer

Complete the implementation of the function below, which minimizes a
quadratic function $\frac12 x^T Qx$ (with no or constant terms) over a
convex set $C$.

``` julia
"""
Projected gradient method for the quadratic optimization problem

    minimize_{x}  1/2 x'Qx  subj to  x ∈ C.

The function `proj(b)` compute the projection of the vector `b` onto the convex set 𝒞.
"""
function pgrad(Q, proj::Function; maxits=100, ϵ=1e-5)
    # your code here
    return x
end;
```

### 3.3 Compute a minimum-risk portfolio

Use the function `pgrad` to obtain the minimum-risk portfolio from a set
of assets with returns `r` and covariances `Σ`. Use `proj_intersection`
as the input projection function for `pgrad`.

``` julia
"""
Given a set of `n` assets with expected returns `r` and covariance matrix `Σ`, compute the minimum-risk portfolio with expected return `μ`.
"""
function efficient_portfolio(r, Σ, μ)
    n = length(r)
    p1 = # your code here
    p2 = # your code here 
    p = b -> proj_intersection(b, p1, p2, maxits=10000, ϵ=1e-8)
    x = pgrad(Σ, p, maxits=1000)
end;
```

Here we use the function `efficient_portfolio` to compute an optimal
portfolio with expected return of 10%. Show in a pie chart the
allocation of the portfolio among the stocks.

In [1]:
xp1 = efficient_portfolio(r, Σ, .1)
pie(stocks, xp1, title="Portfolio Allocation")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip160)" d="M1102.39 32.4315 Q1096.39 32.4315 1092.91 37.1306 Q1089.43 41.7891 1089.43 49.9314 Q1089.43 58.0738 1092.87 62.7728 Q1096.35 67.4314 1102.39 67.4314 Q1108.34 67.4314 1111.83 62.7323 Q1115.31 58.0333 1115.31 49.9314 Q1115.31 41.8701 1111.83 37.1711 Q1108.34 32.4315 1102.39 32.4315 M1102.39 26.1121 Q1112.11 26.1121 1117.66 32.4315 Q1123.21 38.7509 1123.21 49.9314 Q1123.21 61.0714 1117.66 67.4314 Q1112.11 73.7508 1102.39 73.7508 Q1092.63 73.7508 1087.08 67.4314 Q1081.57 61.0714 1081.57 49.9314 Q1081.57 38.7509 1087.08 32.4315 Q1092.63 26.1121 1102.39 26.1121 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip160)" d="M1248.99 32.4315 Q1243 32.4315 1239.51 37.1306 Q1236.03 41.7891 1236.03 49.9314 Q1236.03 58.0738 1239.47 62.7728 Q1242.96 67.4314 1248.99 67.4314 Q1254.95 67.4314 1258.43 62.7323 Q1261.91 58.0333 1261.91 49.9314 Q1261.91 41.8701 1258.43 37.1711 Q1254.95 32.4315 1248.99 32.4315 M1248.99 26.1121 Q1258.71 26.1121 1264.26 32.4315 Q1269.81 38.7509 1269.81 49.9314 Q1269.81 61.0714 1264.26 67.4314 Q1258.71 73.7508 1248.99 73.7508 Q1239.23 73.7508 1233.68 67.4314 Q1228.17 61.0714 1228.17 49.9314 Q1228.17 38.7509 1233.68 32.4315 Q1239.23 26.1121 1248.99 26.1121 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip160)" d="M1345.85 32.4315 Q1339.85 32.4315 1336.37 37.1306 Q1332.89 41.7891 1332.89 49.9314 Q1332.89 58.0738 1336.33 62.7728 Q1339.81 67.4314 1345.85 67.4314 Q1351.8 67.4314 1355.29 62.7323 Q1358.77 58.0333 1358.77 49.9314 Q1358.77 41.8701 1355.29 37.1711 Q1351.8 32.4315 1345.85 32.4315 M1345.85 26.1121 Q1355.57 26.1121 1361.12 32.4315 Q1366.67 38.7509 1366.67 49.9314 Q1366.67 61.0714 1361.12 67.4314 Q1355.57 73.7508 1345.85 73.7508 Q1336.09 73.7508 1330.54 67.4314 Q1325.03 61.0714 1325.03 49.9314 Q1325.03 38.7509 1330.54 32.4315 Q1336.09 26.1121 1345.85 26.1121 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip160)" d="M1525.83 32.4315 Q1519.84 32.4315 1516.35 37.1306 Q1512.87 41.7891 1512.87 49.9314 Q1512.87 58.0738 1516.31 62.7728 Q1519.8 67.4314 1525.83 67.4314 Q1531.79 67.4314 1535.27 62.7323 Q1538.75 58.0333 1538.75 49.9314 Q1538.75 41.8701 1535.27 37.1711 Q1531.79 32.4315 1525.83 32.4315 M1525.83 26.1121 Q1535.55 26.1121 1541.1 32.4315 Q1546.65 38.7509 1546.65 49.9314 Q1546.65 61.0714 1541.1 67.4314 Q1535.55 73.7508 1525.83 73.7508 Q1516.07 73.7508 1510.52 67.4314 Q1505.01 61.0714 1505.01 49.9314 Q1505.01 38.7509 1510.52 32.4315 Q1516.07 26.1121 1525.83 26.1121 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip160)" d="M1591.66 28.9478 L1591.66 35.9153 Q1588.5 34.1734 1585.3 33.3227 Q1582.14 32.4315 1578.9 32.4315 Q1571.65 32.4315 1567.64 37.0496 Q1563.63 41.6271 1563.63 49.9314 Q1563.63 58.2358 1567.64 62.8538 Q1571.65 67.4314 1578.9 67.4314 Q1582.14 67.4314 1585.3 66.5807 Q1588.5 65.6895 1591.66 63.9476 L1591.66 70.8341 Q1588.54 72.2924 1585.18 73.0216 Q1581.86 73.7508 1578.09 73.7508 Q1567.84 73.7508 1561.8 67.3098 Q1555.77 60.8689 1555.77 49.9314 Q1555.77 38.832 1561.84 32.472 Q1567.96 26.1121 1578.57 26.1121 Q1582.02 26.1121 1585.3 26.8413 Q1588.58 27.5299 1591.66 28.9478 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip160)" d="M1625.24 49.7694 Q1616.21 49.7694 1612.72 51.8354 Q1609.24 53.9013 1609.24 58.8839 Q1609.24 62.8538 1611.83 65.2034 Q1614.46 67.5124 1618.96 67.5124 Q1625.16 67.5124 1628.89 63.1374 Q1632.65 58.7219 1632.65 51.4303 L1632.65 49.7694 L1625.24 49.7694 M1640.11 46.6907 L1640.11 72.576 L1632.65 72.576 L1632.65 65.6895 Q1630.1 69.8214 1626.29 71.8063 Q1622.49 73.7508 1616.98 73.7508 Q1610.01 73.7508 1605.88 69.8619 Q1601.79 65.9325 1601.79 59.3701 Q1601.79 51.7138 1606.89 47.825 Q1612.03 43.9361 1622.2 43.9361 L1632.65 43.9361 L1632.65 43.2069 Q1632.65 38.0623 1629.25 35.2672 Q1625.89 32.4315 1619.77 32.4315 Q1615.8

### 3.4 Compute the efficient frontier (optional)

The *efficient frontier* is the set of optimal portfolios that offer the
minimum risk for a given expected rate of return. Use the function
`efficient_portfolio` to compute the efficient frontier for expected
rates of return between 0 and 10%. Plot the objective value (risk) for
10 values of expected return between 0 and 10%.

``` julia
# Define target returns
target_returns = range(0, 0.1, length=10)

# Initialize arrays to store results
portfolio_risks = Float64[]
portfolio_returns = Float64[]

# Loop over target returns
for μ in target_returns
  # your code here
end
```

Plot the efficient frontier.

In [1]:
plot(portfolio_returns, portfolio_risks, label="Efficient Frontier", 
    xlabel="Return", ylabel="Risk", title="Portfolio Risk vs Return")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip220)" d="M356.449 1767.34 Q352.838 1767.34 351.01 1770.9 Q349.204 1774.45 349.204 1781.58 Q349.204 1788.68 351.01 1792.25 Q352.838 1795.79 356.449 1795.79 Q360.084 1795.79 361.889 1792.25 Q363.718 1788.68 363.718 1781.58 Q363.718 1774.45 361.889 1770.9 Q360.084 1767.34 356.449 1767.34 M356.449 1763.64 Q362.26 1763.64 365.315 1768.24 Q368.394 1772.83 368.394 1781.58 Q368.394 1790.3 365.315 1794.91 Q362.26 1799.49 356.449 1799.49 Q350.639 1799.49 347.561 1794.91 Q344.505 1790.3 344.505 1781.58 Q344.505 1772.83 347.561 1768.24 Q350.639 1763.64 356.449 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip220)" d="M401.681 1767.34 Q398.07 1767.34 396.241 1770.9 Q394.435 1774.45 394.435 1781.58 Q394.435 1788.68 396.241 1792.25 Q398.07 1795.79 401.681 1795.79 Q405.315 1795.79 407.12 1792.25 Q408.949 1788.68 408.949 1781.58 Q408.949 1774.45 407.12 1770.9 Q405.315 1767.34 401.681 1767.34 M401.681 1763.64 Q407.491 1763.64 410.546 1768.24 Q413.625 1772.83 413.625 1781.58 Q413.625 1790.3 410.546 1794.91 Q407.491 1799.49 401.681 1799.49 Q395.87 1799.49 392.792 1794.91 Q389.736 1790.3 389.736 1781.58 Q389.736 1772.83 392.792 1768.24 Q395.87 1763.64 401.681 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip220)" d="M425.87 1794.89 L442.19 1794.89 L442.19 1798.82 L420.245 1798.82 L420.245 1794.89 Q422.907 1792.13 427.491 1787.5 Q432.097 1782.85 433.278 1781.51 Q435.523 1778.98 436.403 1777.25 Q437.305 1775.49 437.305 1773.8 Q437.305 1771.04 435.361 1769.31 Q433.44 1767.57 430.338 1767.57 Q428.139 1767.57 425.685 1768.34 Q423.255 1769.1 420.477 1770.65 L420.477 1765.93 Q423.301 1764.79 425.755 1764.21 Q428.208 1763.64 430.245 1763.64 Q435.616 1763.64 438.81 1766.32 Q442.004 1769.01 442.004 1773.5 Q442.004 1775.63 441.194 1777.55 Q440.407 1779.45 438.301 1782.04 Q437.722 1782.71 434.62 1785.93 Q431.518 1789.12 425.87 1794.89 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip220)" d="M900.599 1767.34 Q896.988 1767.34 895.159 1770.9 Q893.353 1774.45 893.353 1781.58 Q893.353 1788.68 895.159 1792.25 Q896.988 1795.79 900.599 1795.79 Q904.233 1795.79 906.039 1792.25 Q907.867 1788.68 907.867 1781.58 Q907.867 1774.45 906.039 1770.9 Q904.233 1767.34 900.599 1767.34 M900.599 1763.64 Q906.409 1763.64 909.464 1768.24 Q912.543 1772.83 912.543 1781.58 Q912.543 1790.3 909.464 1794.91 Q906.409 1799.49 900.599 1799.49 Q894.789 1799.49 891.71 1794.91 Q888.654 1790.3 888.654 1781.58 Q888.654 1772.83 891.71 1768.24 Q894.789 1763.64 900.599 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip220)" d="M945.83 1767.34 Q942.219 1767.34 940.39 1770.9 Q938.585 1774.45 938.585 1781.58 Q938.585 1788.68 940.39 1792.25 Q942.219 1795.79 945.83 1795.79 Q949.464 1795.79 951.27 1792.25 Q953.098 1788.68 953.098 1781.58 Q953.098 1774.45 951.27 1770.9 Q949.464 1767.34 945.83 1767.34 M945.83 1763.64 Q951.64 1763.64 954.696 1768.24 Q957.774 1772.83 957.774 1781.58 Q957.774 1790.3 954.696 1794.91 Q951.64 1799.49 945.83 1799.49 Q940.02 1799.49 936.941 1794.91 Q933.886 1790.3 933.886 1781.58 Q933.886 1772.83 936.941 1768.24 Q940.02 1763.64 945.83 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip220)" d="M1445.95 1767.34 Q1442.34 1767.34 1440.51 1770.9 Q1438.71 1774.45 1438.71 1781.58 Q1438.71 1788.68 1440.51 1792.25 Q1442.34 1795.79 1445.95 1795.79 Q1449.59 1795.79 1451.39 1792.25 Q1453.22 1788.68 1453.22 1781.58 Q1453.22 1774.45 1451.39 1770.9 Q1449.59 1767.34 1445.95 1767.34 M1445.95 1763.64 Q1451.76 1763.64 1454.82 1768.24 Q1457.9 1772.83 1457.9 1781.58 Q1457.9 1790.3 1454.82 1794.91 Q1451.76 1799.49 1445.95 1799.49 Q1440.14 1799.49 1437.06 1794.91 Q1434.01 1790.3 1434.01 1781.58 Q1434.01 1772.83 1437.06 1768.24 Q1440.14 1763.64 1445.95 1763.64 Z" fill="#000000"